# Incidence de la varicelle

## Chargement des données

In [32]:
%matplotlib inline
import pandas as pd
import matplotlib.pyplot as plt
import isoweek

On commence par récupérer les données depuis le site [Réseau Sentinelles](https://www.sentiweb.fr/france/fr/?) en naviguant dans le menu de gauche: `Surveillance continue`-> `Bases de données` puis `Accès aux données`. On sélectionne `Varicelle (1991 - en cours)` dans le menu déroulant intitulé `Maladie/Indicateur` puis, dans l'onglet `Télécharger` on prend soin de télécharger les données au format CSV afin de déterminer l'URL permettant d'accéder à ces données. Celle-ci est stockée sous la forme d'une chaîne de caractères dans la variable suivante:

In [33]:
data_url = "https://www.sentiweb.fr/datasets/incidence-PAY-7.csv"

La lecture des données brutes donne:

In [34]:
raw_data = pd.read_csv(data_url, encoding = 'iso-8859-1', skiprows=1)
raw_data

week  indicator    inc  inc_low  inc_up  inc100  inc100_low  \
0     202203          7  14299    10896   17702      22          17   
1     202202          7   8506     6034   10978      13           9   
2     202201          7  13793    10597   16989      21          16   
3     202152          7  13239     9611   16867      20          15   
4     202151          7  13326     9629   17023      20          14   
5     202150          7  14128    10312   17944      21          15   
6     202149          7  13674    10369   16979      21          16   
7     202148          7  11549     8503   14595      17          12   
8     202147          7  11419     8376   14462      17          12   
9     202146          7   8216     5724   10708      12           8   
10    202145          7   8965     6468   11462      14          10   
11    202144          7   8736     5636   11836      13           8   
12    202143          7   8145     5164   11126      12           7   
13    202142          7   9443     6037   12849      14           9   
14    202141          7   4021     2239    5803       6           3   
15    202140          7   4441     2454    6428       7           4   
16    202139          7   2291     1056    3526       3           1   
17    202138          7   4325     2267    6383       7           4   
18    202137          7   1964      754    3174       3           1   
19    202136          7   3441     1730    5152       5           2   
20    202135          7   2562     1107    4017       4           2   
21    202134          7   1429      378    2480       2           0   
22    202133          7   3829     1830    5828       6           3   
23    202132          7   4108     1895    6321       6           3   
24    202131          7   4793     2301    7285       7           3   
25    202130          7   7190     4191   10189      11           6   
26    202129          7   6800     4109    9491      10           6   
27    202128          7   9734        0   21731      15           0   
28    202127          7   9026     4316   13736      14           7   
29    202126          7   7284     4108   10460      11           6   
...      ...        ...    ...      ...     ...     ...         ...   
1595  199126          7  17608    11304   23912      31          20   
1596  199125          7  16169    10700   21638      28          18   
1597  199124          7  16171    10071   22271      28          17   
1598  199123          7  11947     7671   16223      21          13   
1599  199122          7  15452     9953   20951      27          17   
1600  199121          7  14903     8975   20831      26          16   
1601  199120          7  19053    12742   25364      34          23   
1602  199119          7  16739    11246   22232      29          19   
1603  199118          7  21385    13882   28888      38          25   
1604  199117          7  13462     8877   18047      24          16   
1605  199116          7  14857    10068   19646      26          18   
1606  199115          7  13975     9781   18169      25          18   
1607  199114          7  12265     7684   16846      22          14   
1608  199113          7   9567     6041   13093      17          11   
1609  199112          7  10864     7331   14397      19          13   
1610  199111          7  15574    11184   19964      27          19   
1611  199110          7  16643    11372   21914      29          20   
1612  199109          7  13741     8780   18702      24          15   
1613  199108          7  13289     8813   17765      23          15   
1614  199107          7  12337     8077   16597      22          15   
1615  199106          7  10877     7013   14741      19          12   
1616  199105          7  10442     6544   14340      18          11   
1617  199104          7   7913     4563   11263      14           8   
1618  199103          7  15387    10484   20290      27          18   
1619  199102          7  16277  

## Reformatage des données

Dans un premier temps, on vérifie s'il n'y a pas de lignes manquantes dans le tableau ci-dessus:

In [35]:
missing_lines = raw_data[raw_data.isnull().any(axis=1)]
missing_lines

Empty DataFrame
Columns: [week, indicator, inc, inc_low, inc_up, inc100, inc100_low, inc100_up, geo_insee, geo_name]
Index: []

On voit que la variable `missing_lines` est vide, ce qui indique que le jeux de données ne souffre pas de "trous". On copie le jeu de données dans une nouvelle variable, qui est celle sur laquelle les traitements seront effectués:

In [36]:
data = raw_data

Ensuite, on reformule la numérotation des semaines. En effet, dans le tableau ci-dessus, les semaines sont numérotées avec six chiffres: les quatres premiers chiffres correspondent à l'année, et les deux derniers au numéro de la semaine, ce qui donne l'impression à `pandas` qu'il s'agit d'un entier alors que ce n'est pas le cas. De plus, une telle numérotation ne peut pas être interprétée par `pandas`, il faut donc la reformuler. Cela est réalisé avec la librairie `isoweek`. On écrit une fonction `conversionDate`qui sera appliquée à l'ensemble de la première colonne du jeu de données:

In [40]:
def conversionDate(dateInt):
    
    dateStr = str(dateInt)
    annee = int(dateStr[:4])
    semaine = int(dateStr[4:])
    s = isoweek.Week(annee, semaine)
    return pd.Period(s.day(0), 'W')

In [41]:
data["period"] = data["week"].apply(conversionDate)
data

week  indicator    inc  inc_low  inc_up  inc100  inc100_low  \
0     202203          7  14299    10896   17702      22          17   
1     202202          7   8506     6034   10978      13           9   
2     202201          7  13793    10597   16989      21          16   
3     202152          7  13239     9611   16867      20          15   
4     202151          7  13326     9629   17023      20          14   
5     202150          7  14128    10312   17944      21          15   
6     202149          7  13674    10369   16979      21          16   
7     202148          7  11549     8503   14595      17          12   
8     202147          7  11419     8376   14462      17          12   
9     202146          7   8216     5724   10708      12           8   
10    202145          7   8965     6468   11462      14          10   
11    202144          7   8736     5636   11836      13           8   
12    202143          7   8145     5164   11126      12           7   
13    202142          7   9443     6037   12849      14           9   
14    202141          7   4021     2239    5803       6           3   
15    202140          7   4441     2454    6428       7           4   
16    202139          7   2291     1056    3526       3           1   
17    202138          7   4325     2267    6383       7           4   
18    202137          7   1964      754    3174       3           1   
19    202136          7   3441     1730    5152       5           2   
20    202135          7   2562     1107    4017       4           2   
21    202134          7   1429      378    2480       2           0   
22    202133          7   3829     1830    5828       6           3   
23    202132          7   4108     1895    6321       6           3   
24    202131          7   4793     2301    7285       7           3   
25    202130          7   7190     4191   10189      11           6   
26    202129          7   6800     4109    9491      10           6   
27    202128          7   9734        0   21731      15           0   
28    202127          7   9026     4316   13736      14           7   
29    202126          7   7284     4108   10460      11           6   
...      ...        ...    ...      ...     ...     ...         ...   
1595  199126          7  17608    11304   23912      31          20   
1596  199125          7  16169    10700   21638      28          18   
1597  199124          7  16171    10071   22271      28          17   
1598  199123          7  11947     7671   16223      21          13   
1599  199122          7  15452     9953   20951      27          17   
1600  199121          7  14903     8975   20831      26          16   
1601  199120          7  19053    12742   25364      34          23   
1602  199119          7  16739    11246   22232      29          19   
1603  199118          7  21385    13882   28888      38          25   
1604  199117          7  13462     8877   18047      24          16   
1605  199116          7  14857    10068   19646      26          18   
1606  199115          7  13975     9781   18169      25          18   
1607  199114          7  12265     7684   16846      22          14   
1608  199113          7   9567     6041   13093      17          11   
1609  199112          7  10864     7331   14397      19          13   
1610  199111          7  15574    11184   19964      27          19   
1611  199110          7  16643    11372   21914      29          20   
1612  199109          7  13741     8780   18702      24          15   
1613  199108          7  13289     8813   17765      23          15   
1614  199107          7  12337     8077   16597      22          15   
1615  199106          7  10877     7013   14741      19          12   
1616  199105          7  10442     6544   14340      18          11   
1617  199104          7   7913     4563   11263      14           8   
1618  199103          7  15387    10484   20290      27          18   
1619  199102          7  16277  

Ensuite, on définit la colonne nouvellement créée comme le nouvel index de nos données:

In [43]:
data = data.set_index("period")

Puis on trie les données par ordre chronologique:

In [46]:
data = data.sort_index()